## April 3 - More Learning - Statistics and Naive Bayes

Mostly chapter 18 and 20 from AIMA

In [235]:
from learning import *
from notebook import *

In [236]:
iris = DataSet(name="iris")

## NAIVE BAYES LEARNER

### Overview

#### Theory of Probabilities

The Naive Bayes algorithm is a probabilistic classifier, making use of [Bayes' Theorem](https://en.wikipedia.org/wiki/Bayes%27_theorem). The theorem states that the conditional probability of <b>A</b> given <b>B</b> equals the conditional probability of <b>B</b> given <b>A</b> multiplied by the probability of <b>A</b>, divided by the probability of <b>B</b>.

$$P(A|B) = \dfrac{P(B|A)*P(A)}{P(B)}$$

From the theory of Probabilities we have the Multiplication Rule, if the events *X* are independent the following is true:

$$P(X_{1} \cap X_{2} \cap ... \cap X_{n}) = P(X_{1})*P(X_{2})*...*P(X_{n})$$

For conditional probabilities this becomes:

$$P(X_{1}, X_{2}, ..., X_{n}|Y) = P(X_{1}|Y)*P(X_{2}|Y)*...*P(X_{n}|Y)$$

#### Classifying an Item

How can we use the above to classify an item though?

We have a dataset with a set of classes (<b>C</b>) and we want to classify an item with a set of features (<b>F</b>). Essentially what we want to do is predict the class of an item given the features.

For a specific class, <b>Class</b>, we will find the conditional probability given the item features:

$$P(Class|F) = \dfrac{P(F|Class)*P(Class)}{P(F)}$$

We will do this for every class and we will pick the maximum. This will be the class the item is classified in.

The features though are a vector with many elements. We need to break the probabilities up using the multiplication rule. Thus the above equation becomes:

$$P(Class|F) = \dfrac{P(Class)*P(F_{1}|Class)*P(F_{2}|Class)*...*P(F_{n}|Class)}{P(F_{1})*P(F_{2})*...*P(F_{n})}$$

The calculation of the conditional probability then depends on the calculation of the following:

*a)* The probability of <b>Class</b> in the dataset.

*b)* The conditional probability of each feature occurring in an item classified in <b>Class</b>.

*c)* The probabilities of each individual feature.

For *a)*, we will count how many times <b>Class</b> occurs in the dataset (aka how many items are classified in a particular class).

For *b)*, if the feature values are discrete ('Blue', '3', 'Tall', etc.), we will count how many times a feature value occurs in items of each class. If the feature values are not discrete, we will go a different route. We will use a distribution function to calculate the probability of values for a given class and feature. If we know the distribution function of the dataset, then great, we will use it to compute the probabilities. If we don't know the function, we can assume the dataset follows the normal (Gaussian) distribution without much loss of accuracy. In fact, it can be proven that any distribution tends to the Gaussian the larger the population gets (see [Central Limit Theorem](https://en.wikipedia.org/wiki/Central_limit_theorem)).

*NOTE:* If the values are continuous but use the discrete approach, there might be issues if we are not lucky. For one, if we have two values, '5.0 and 5.1', with the discrete approach they will be two completely different values, despite being so close. Second, if we are trying to classify an item with a feature value of '5.15', if the value does not appear for the feature, its probability will be 0. This might lead to misclassification. Generally, the continuous approach is more accurate and more useful, despite the overhead of calculating the distribution function.

The last one, *c)*, is tricky. If feature values are discrete, we can count how many times they occur in the dataset. But what if the feature values are continuous? Imagine a dataset with a height feature. Is it worth it to count how many times each value occurs? Most of the time it is not, since there can be miscellaneous differences in the values (for example, 1.7 meters and 1.700001 meters are practically equal, but they count as different values).

So as we cannot calculate the feature value probabilities, what are we going to do?

Let's take a step back and rethink exactly what we are doing. We are essentially comparing conditional probabilities of all the classes. For two classes, <b>A</b> and <b>B</b>, we want to know which one is greater:

$$\dfrac{P(F|A)*P(A)}{P(F)} vs. \dfrac{P(F|B)*P(B)}{P(F)}$$

Wait, <b>P(F)</b> is the same for both the classes! In fact, it is the same for every combination of classes. That is because <b>P(F)</b> does not depend on a class, thus being independent of the classes.

So, for *c)*, we actually don't need to calculate it at all.

#### Wrapping It Up

Classifying an item to a class then becomes a matter of calculating the conditional probabilities of feature values and the probabilities of classes. This is something very desirable and computationally delicious.

Remember though that all the above are true because we made the assumption that the features are independent. In most real-world cases that is not true though. Is that an issue here? Fret not, for the the algorithm is very efficient even with that assumption. That is why the algorithm is called **Naive** Bayes Classifier. We (naively) assume that the features are independent to make computations easier.

### Implementation

The implementation of the Naive Bayes Classifier is split in two; *Learning* and *Simple*. The *learning* classifier takes as input a dataset and learns the needed distributions from that. It is itself split into two, for discrete and continuous features. The *simple* classifier takes as input not a dataset, but already calculated distributions (a dictionary of `CountingProbDist` objects).

#### Discrete

The implementation for discrete values counts how many times each feature value occurs for each class, and how many times each class occurs. The results are stored in a `CountinProbDist` object.

With the below code you can see the probabilities of the class "Setosa" appearing in the dataset and the probability of the first feature (at index 0) of the same class having a value of 5. Notice that the second probability is relatively small, even though if we observe the dataset we will find that a lot of values are around 5. The issue arises because the features in the Iris dataset are continuous, and we are assuming they are discrete. If the features were discrete (for example, "Tall", "3", etc.) this probably wouldn't have been the case and we would see a much nicer probability distribution.

In [237]:
psource(CountingProbDist)

### Statistical Learning

Chapter 20, page 802

We briefly digress from the iris dataset.

There are five types of bags of candies.  Each bag has 100 pieces, individually wrapped.  One bag has all cherry (yum).
One bag has all lime (yuck).  The wrapping paper is identical and opaque.

Three other bags have a mixture: (75 cherry, 25 lime), (50 each), (25 cherry, 75 lime).

The bags themselves are not evenly distributed.  10% are all cherry and 10% are all lime.  40% are 50/50, and 20% are either 25% lime or 25% cherry.

If I give you a bag at random, you can randomly sample one candy at a time (and then rewrap it put it back in the bag).

You pick a random bag and start sampling.  If you select one lime candy, what is the most likely bag? What if you pick two in row?  Three in row? Four in a row?

We can use the CountingProbDist() to model this problem.

In [238]:
h1 = CountingProbDist('c'*100)
h2 = CountingProbDist('c'*75+'l'*25)
h3 = CountingProbDist('c'*50+'l'*50)
h4 = CountingProbDist('c'*25+'l'*75)
h5 = CountingProbDist('l'*100)
dist = {('h1', 0.1): h1, ('h2', 0.2): h2, ('h3', 0.4): h3, 
        ('h4', 0.2): h4, ('h5', 0.1): h5}
nBS = NaiveBayesLearner(dist, simple=True)

The NaiveBayesLearner is actually three functions.  Here we are using the simple one.

In [239]:
'c'*100

'cccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccc'

In [240]:
h2.dictionary

{'c': 75, 'l': 25}

In [241]:
psource(NaiveBayesLearner)

In [242]:
dir(h1)

['__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__getitem__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 'add',
 'default',
 'dictionary',
 'n_obs',
 'sample',
 'sampler',
 'smooth_for',
 'top']

In [243]:
h1.dictionary

{'c': 100}

In [244]:
h1.sample()

'c'

In [245]:
h3.dictionary

{'c': 50, 'l': 50}

In [246]:
h3.sample()

'c'

We can practice our $\LaTeX{}$

$ h1: 100\%$ cherry

$ h2: 75\%$ cherry $+ 25\%$ lime,

$ h3: 50\%$ cherry $+ 50\%$ lime,

$ h4: 25\%$ cherry $+ 75\%$ lime,

$ h5: 100\%$ lime.

$$P(h1) = 10\%$$
$$P(h2) = 20\%$$
$$P(h3) = 40\%$$
$$P(h4) = 20\%$$
$$P(h5) = 10\%$$

$$P(h_{i}|lime) = \alpha{}P(lime|h_{i}) P(h_{i}) $$

**Bayesian learning** simply calculates the probability of each hypothesis, given the data, and makes predictions on that basis.

So, if we pick a random bag of candy and draw a lime flavored treat, we can calculate which bag is most likely.

$$P(h_{1}|lime) = \alpha{}P(lime|h_{1}) P(h_{1}) = 0 * .1 = 0 $$
$$P(h_{2}|lime) = \alpha{}P(lime|h_{2}) P(h_{2}) = .25 * .2 = .125 $$
$$P(h_{3}|lime) = \alpha{}P(lime|h_{3}) P(h_{3}) = .5 * .4 = .2 $$
$$P(h_{4}|lime) = \alpha{}P(lime|h_{4}) P(h_{4}) = .25 * .2 = .125 $$
$$P(h_{5}|lime) = \alpha{}P(lime|h_{5}) P(h_{5}) = 1 * .1 = .1$$

Thus, the most likely hypothesis is $h_3$ at 20%.

See Figure 20.1 on page 804

In [247]:
print (nBS('l'))
print (nBS('ll'))
print (nBS('lll'))
print (nBS('llll'))

h3
h4
h5
h5


In [248]:
psource(NaiveBayesSimple)

Now we will disect the code.  The point is there is no magic.  We are just performing vanilla probability calculations.

In [249]:
target_dist = {c_name: prob for c_name, prob in dist.keys()}
target_dist

{'h1': 0.1, 'h2': 0.2, 'h3': 0.4, 'h4': 0.2, 'h5': 0.1}

In [250]:
attr_dists = {c_name: count_prob for (c_name, _), count_prob in dist.items()}
attr_dists

{'h1': <learning.CountingProbDist at 0x7f02c4c51b10>,
 'h2': <learning.CountingProbDist at 0x7f02c4c51710>,
 'h3': <learning.CountingProbDist at 0x7f02c4c51590>,
 'h4': <learning.CountingProbDist at 0x7f02c4c51310>,
 'h5': <learning.CountingProbDist at 0x7f02c4c51a90>}

In [251]:
def class_probability(targetval):
            attr_dist = attr_dists[targetval]
            return target_dist[targetval] * product(attr_dist[a] for a in example)

In [252]:
example = 'll'
argmax(target_dist.keys(), key=class_probability)

'h4'

In [255]:
example = 'll'
list(map(class_probability, target_dist.keys()))

[0.0, 0.0125, 0.1, 0.1125, 0.1]

### Back to the flowers

It is spring, you know.


In [256]:
dataset = iris

target_vals = dataset.values[dataset.target]
target_dist = CountingProbDist(target_vals)
attr_dists = {(gv, attr): CountingProbDist(dataset.values[attr])
              for gv in target_vals
              for attr in dataset.inputs}
for example in dataset.examples:
        targetval = example[dataset.target]
        target_dist.add(targetval)
        for attr in dataset.inputs:
            attr_dists[targetval, attr].add(example[attr])


print(target_dist['setosa'])
print(attr_dists['setosa', 0][5.0])
print(attr_dists['setosa', 0][6.0])

0.3333333333333333
0.10588235294117647
0.011764705882352941


In [197]:
attr_dists

{('virginica', 0): <learning.CountingProbDist at 0x7f02c4dad390>,
 ('virginica', 1): <learning.CountingProbDist at 0x7f02c4cdf5d0>,
 ('virginica', 2): <learning.CountingProbDist at 0x7f02c4cdfa90>,
 ('virginica', 3): <learning.CountingProbDist at 0x7f02c4cdf1d0>,
 ('versicolor', 0): <learning.CountingProbDist at 0x7f02c4cdf390>,
 ('versicolor', 1): <learning.CountingProbDist at 0x7f02c4cdf210>,
 ('versicolor', 2): <learning.CountingProbDist at 0x7f02c4cdf890>,
 ('versicolor', 3): <learning.CountingProbDist at 0x7f02c4cdffd0>,
 ('setosa', 0): <learning.CountingProbDist at 0x7f02c4cdf8d0>,
 ('setosa', 1): <learning.CountingProbDist at 0x7f02c4cdfb90>,
 ('setosa', 2): <learning.CountingProbDist at 0x7f02c4cdf810>,
 ('setosa', 3): <learning.CountingProbDist at 0x7f02c4cdf990>}

In [198]:
target_dist

First we found the different values for the classes (called targets here) and calculated their distribution. Next we initialized a dictionary of `CountingProbDist` objects, one for each class and feature. Finally, we iterated through the examples in the dataset and calculated the needed probabilites.

Having calculated the different probabilities, we will move on to the predicting function. It will receive as input an item and output the most likely class. Using the above formula, it will multiply the probability of the class appearing, with the probability of each feature value appearing in the class. It will return the max result.

In [257]:
def predict(example):
    def class_probability(targetval):
        return (target_dist[targetval] *
                product(attr_dists[targetval, attr][example[attr]]
                        for attr in dataset.inputs))
    return argmax(target_vals, key=class_probability)


print(predict([5, 3, 1, 0.1]))

setosa


You can view the complete code by executing the next line, which combines the above code:

In [200]:
psource(NaiveBayesDiscrete)

#### Continuous

In the implementation we use the Gaussian/Normal distribution function. To make it work, we need to find the means and standard deviations of features for each class. We make use of the `find_means_and_deviations` Dataset method. On top of that, we will also calculate the class probabilities as we did with the Discrete approach.

In [201]:
psource (DataSet)

In [258]:
means, deviations = dataset.find_means_and_deviations()

target_vals = dataset.values[dataset.target]
target_dist = CountingProbDist(target_vals)

print ('setosa:')
print('means: ' + str(means["setosa"]))
print('deviations: ' + str(deviations["setosa"]))
print ('versicolor:')
print('means: ' + str(means["versicolor"]))
print('deviations: ' + str(deviations["versicolor"]))

setosa:
means: [5.006, 3.418, 1.464, 0.244]
deviations: [0.3524896872134513, 0.38102439795469095, 0.17351115943644546, 0.10720950308167838]
versicolor:
means: [5.936, 2.77, 4.26, 1.326]
deviations: [0.5161711470638634, 0.3137983233784114, 0.46991097723995795, 0.19775268000454405]


You can see the means of the features for the "Setosa" class and the deviations for "Versicolor".

The prediction function will work similarly to the Discrete algorithm. It will multiply the probability of the class occurring with the conditional probabilities of the feature values for the class.

Since we are using the Gaussian distribution, we will input the value for each feature into the Gaussian function, together with the mean and deviation of the feature. This will return the probability of the particular feature value for the given class. We will repeat for each class and pick the max value.

In [259]:
def predict(example):
    def class_probability(targetval):
        prob = target_dist[targetval]
        for attr in dataset.inputs:
            prob *= gaussian(means[targetval][attr], deviations[targetval][attr], example[attr])
        return prob

    return argmax(target_vals, key=class_probability)


print(predict([5, 3, 1, 0.1]))

setosa


The complete code of the continuous algorithm:

In [204]:
psource(NaiveBayesContinuous)

#### Simple

The simple classifier (chosen with the argument `simple`) does not learn from a dataset, instead it takes as input a dictionary of already calculated `CountingProbDist` objects and returns a predictor function. The dictionary is in the following form: `(Class Name, Class Probability): CountingProbDist Object`.

Each class has its own probability distribution. The classifier given a list of features calculates the probability of the input for each class and returns the max. The only pre-processing work is to create dictionaries for the distribution of classes (named `targets`) and attributes/features.


This classifier is useful when you already have calculated the distributions and you need to predict future items.

### Examples

We will now use the Naive Bayes Classifier (Discrete and Continuous) to classify items:

In [260]:
nBD = NaiveBayesLearner(iris, continuous=False)
print("Discrete Classifier")
print(nBD([5, 3, 1, 0.1]))
print(nBD([6, 5, 3, 1.5]))
print(nBD([7, 3, 6.5, 2]))


nBC = NaiveBayesLearner(iris, continuous=True)
print("\nContinuous Classifier")
print(nBC([5, 3, 1, 0.1]))
print(nBC([6, 5, 3, 1.5]))
print(nBC([7, 3, 6.5, 2]))

Discrete Classifier
setosa
virginica
virginica

Continuous Classifier
setosa
versicolor
virginica


Notice how the Discrete Classifier misclassified the second item, while the Continuous one had no problem.

Let's now take a look at the simple classifier. First we will come up with a sample problem to solve. Say we are given three bags. Each bag contains three letters ('a', 'b' and 'c') of different quantities. We are given a string of letters and we are tasked with finding from which bag the string of letters came.

Since we know the probability distribution of the letters for each bag, we can use the naive bayes classifier to make our prediction.

In [261]:
bag1 = 'a'*50 + 'b'*30 + 'c'*15
dist1 = CountingProbDist(bag1)
bag2 = 'a'*30 + 'b'*45 + 'c'*20
dist2 = CountingProbDist(bag2)
bag3 = 'a'*20 + 'b'*20 + 'c'*35
dist3 = CountingProbDist(bag3)

Now that we have the `CountingProbDist` objects for each bag/class, we will create the dictionary. We assume that it is equally probable that we will pick from any bag.

In [262]:
dist = {('First', 0.5): dist1, ('Second', 0.3): dist2, ('Third', 0.2): dist3}
nBS = NaiveBayesLearner(dist, simple=True)

Now we can start making predictions:

In [263]:
print(nBS('aab'))        # We can handle strings
print(nBS(['b', 'b']))   # And lists!
print(nBS('ccbcc'))

First
Second
Third


The results make intuitive sense. The first bag has a high amount of 'a's, the second has a high amount of 'b's and the third has a high amount of 'c's. The classifier seems to confirm this intuition.

Note that the simple classifier doesn't distinguish between discrete and continuous values. It just takes whatever it is given. Also, the `simple` option on the `NaiveBayesLearner` overrides the `continuous` argument. `NaiveBayesLearner(d, simple=True, continuous=False)` just creates a simple classifier.

## PERCEPTRON CLASSIFIER

### Overview

The Perceptron is a linear classifier. It works the same way as a neural network with no hidden layers (just input and output). First it trains its weights given a dataset and then it can classify a new item by running it through the network.

Its input layer consists of the item features, while the output layer consists of nodes (also called neurons). Each node in the output layer has *n* synapses (for every item feature), each with its own weight. Then, the nodes find the dot product of the item features and the synapse weights. These values then pass through an activation function (usually a sigmoid). Finally, we pick the largest of the values and we return its index.

Note that in classification problems each node represents a class. The final classification is the class/node with the max output value.

Below you can see a single node/neuron in the outer layer. With <i>f</i> we denote the item features, with *w* the synapse weights, then inside the node we have the dot product and the activation function, <i>g</i>.

![perceptron](images/perceptron.png)

### Implementation

First, we train (calculate) the weights given a dataset, using the `BackPropagationLearner` function of `learning.py`. We then return a function, `predict`, which we will use in the future to classify a new item. The function computes the (algebraic) dot product of the item with the calculated weights for each node in the outer layer. Then it picks the greatest value and classifies the item in the corresponding class.

In [209]:
psource(network)

In [210]:
psource(NNUnit)

We will write a little function to show us what is going on inside a neural network unit.

In [211]:
def showNN(unit):
    return (unit.weights, unit.inputs, unit.value, unit.activation)

In [265]:
psource(PerceptronLearner)

In [264]:
def PerceptronLearnerStub(dataset, learning_rate=0.01, epochs=100):
    """Logistic Regression, NO hidden layer"""
    i_units = len(dataset.inputs)
    o_units = len(dataset.values[dataset.target])
    hidden_layer_sizes = []
    raw_net = network(i_units, hidden_layer_sizes, o_units)
    learned_net = BackPropagationLearner(dataset, raw_net, learning_rate, epochs)
    
    return raw_net, learned_net

Note that the Perceptron is a one-layer neural network, without any hidden layers. So, in `BackPropagationLearner`, we will pass no hidden layers. From that function we get our network, which is just one layer, with the weights calculated.

That function `predict` passes the input/example through the network, calculating the dot product of the input and the weights for each node and returns the class with the max dot product.

### Example

We will train the Perceptron on the iris dataset. Because though the `BackPropagationLearner` works with integer indexes and not strings, we need to convert class names to integers. Then, we will try and classify the item/flower with measurements of 5, 3, 1, 0.1.

In [266]:
iris = DataSet(name="iris")
iris.classes_to_numbers()

perceptron = PerceptronLearner(iris)
print(perceptron([5, 3, 1, 0.1]))
raw_stub, learned_stub = PerceptronLearnerStub(iris)

0


The correct output is 0, which means the item belongs in the first class, "setosa". Note that the Perceptron algorithm is not perfect and may produce false classifications.

In [215]:
raw_stub

[[<learning.NNUnit at 0x7f02c4d6c190>,

Returned by showNN: (weights, inputs, value, activation)

In [216]:
list(map(showNN, raw_stub[0]))

[([], [], 5.9, <function utils.sigmoid(x)>),
 ([], [], 3.0, <function utils.sigmoid(x)>),
 ([], [], 5.1, <function utils.sigmoid(x)>),
 ([], [], 1.8, <function utils.sigmoid(x)>)]

raw_stub[1] is the learned network.  Notice that the input units are themselves NNUnits.

In [217]:
list(map(showNN, raw_stub[1]))

[((0.2737810389749918,
   1.1152308748510247,
   -1.543260339282533,
   -0.9099540533153505),
  0.010482971183120342,
  <function utils.sigmoid(x)>),
 ((0.28446859792661994,
   -0.7426785326773424,
   0.006563536532696342,
   -0.7236381177742321),
  0.1410915282457729,
  <function utils.sigmoid(x)>),
 ((-1.1937395158303523,
   -0.9863025882400674,
   1.8655398919571222,
   1.253005921954526),
  0.8524739962604119,
  <function utils.sigmoid(x)>)]

In [218]:
dir(raw_stub[0][0])

['__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 'activation',
 'inputs',
 'value',
 'weights']

In [219]:
raw_stub[0][2].value

5.1

In [220]:
learned_stub

[[<learning.NNUnit at 0x7f02c4d6c190>,

## LINEAR LEARNER

### Overview

Linear Learner is a model that assumes a linear relationship between the input variables x and the single output variable y. More specifically, that y can be calculated from a linear combination of the input variables x. Linear learner is a quite simple model as the representation of this model is a linear equation.  

The linear equation assigns one scaler factor to each input value or column, called coefficients or weights. One additional coefficient is also added, giving additional degree of freedom and is often called the intercept or the bias coefficient.   
For example :  y = ax1 + bx2 + c .  

### Implementation

Below mentioned is the implementation of Linear Learner.

In [221]:
psource(LinearLearner)

This algorithm first assigns some random weights to the input variables and then based on the error calculated updates the weight for each variable. Finally the prediction is made with the updated weights.  

### Implementation

We will now use the Linear Learner to classify a sample with values: 5.1, 3.0, 1.1, 0.1.

In [271]:
iris = DataSet(name="iris")
iris.classes_to_numbers()

linear_learner = LinearLearner(iris)
print(linear_learner([5, 3, 1, 0.1]))

0.10590907746514296


Now we will try some experiments, varying the learning rate and the epochs. The learning rate show how much to change the weight each time and the epochs are the number of learning cycles. 

Note that the learner starts with random weights, so the results vary from run to run.

In [275]:
iris = DataSet(name="iris")
iris.classes_to_numbers()

linear_learner2 = LinearLearner(iris, learning_rate=.05)
print(linear_learner2([5, 3, 1, 0.1]))

2.121753043130544


In [278]:
iris = DataSet(name="iris")
iris.classes_to_numbers()

linear_learner3 = LinearLearner(iris, epochs=1000)
print(linear_learner3([5, 3, 1, 0.1]))

7.100597551535986


## ENSEMBLE LEARNER

### Overview

Ensemble Learning improves the performance of our model by combining several learners. It improves the stability and predictive power of the model. Ensemble methods are meta-algorithms that combine several machine learning techniques into one predictive model in order to decrease variance, bias, or improve predictions.  



![ensemble_learner.jpg](images/ensemble_learner.jpg)


Some commonly used Ensemble Learning techniques are : 

1. Bagging : Bagging tries to implement similar learners on small sample populations and then takes a mean of all the predictions. It helps us to reduce variance error.

2. Boosting : Boosting is an iterative technique which adjust the weight of an observation based on the last classification. If an observation was classified incorrectly, it tries to increase the weight of this observation and vice versa. It helps us to reduce bias error.

3.  Stacking : This is a very interesting way of combining models. Here we use a learner to combine output from different learners. It can either decrease bias or variance error depending on the learners we use.

### Implementation

Below mentioned is the implementation of Ensemble Learner.

In [225]:
psource(EnsembleLearner)

This algorithm takes input as a list of learning algorithms, have them vote and then finally returns the predicted result.

## LEARNER EVALUATION

In this section we will evaluate and compare algorithm performance. The dataset we will use will again be the iris one.

In [226]:
iris = DataSet(name="iris")

### Naive Bayes

First up we have the Naive Bayes algorithm. First we will test how well the Discrete Naive Bayes works, and then how the Continuous fares.

In [227]:
nBD = NaiveBayesLearner(iris, continuous=False)
print("Error ratio for Discrete:", err_ratio(nBD, iris))

nBC = NaiveBayesLearner(iris, continuous=True)
print("Error ratio for Continuous:", err_ratio(nBC, iris))

Error ratio for Discrete: 0.040000000000000036
Error ratio for Continuous: 0.040000000000000036


The error for the Naive Bayes algorithm is very, very low; close to 0. There is also very little difference between the discrete and continuous version of the algorithm.

## k-Nearest Neighbors

Now we will take a look at kNN, for different values of <i>k</i>. Note that <i>k</i> should have odd values, to break any ties between two classes.

In [228]:
kNN_1 = NearestNeighborLearner(iris, k=1)
kNN_3 = NearestNeighborLearner(iris, k=3)
kNN_5 = NearestNeighborLearner(iris, k=5)
kNN_7 = NearestNeighborLearner(iris, k=7)

print("Error ratio for k=1:", err_ratio(kNN_1, iris))
print("Error ratio for k=3:", err_ratio(kNN_3, iris))
print("Error ratio for k=5:", err_ratio(kNN_5, iris))
print("Error ratio for k=7:", err_ratio(kNN_7, iris))

Error ratio for k=1: 0.0
Error ratio for k=3: 0.06000000000000005
Error ratio for k=5: 0.1266666666666667
Error ratio for k=7: 0.19999999999999996


Notice how the error became larger and larger as <i>k</i> increased. This is generally the case with datasets where classes are spaced out, as is the case with the iris dataset. If items from different classes were closer together, classification would be more difficult. Usually a value of 1, 3 or 5 for *k* suffices.

Also note that since the training set is also the testing set, for *k* equal to 1 we get a perfect score, since the item we want to classify each time is already in the dataset and its closest neighbor is itself.

### Perceptron

For the Perceptron, we first need to convert class names to integers. Let's see how it performs in the dataset.

In [229]:
iris2 = DataSet(name="iris")
iris2.classes_to_numbers()

perceptron = PerceptronLearner(iris2)
print("Error ratio for Perceptron:", err_ratio(perceptron, iris2))

Error ratio for Perceptron: 0.31999999999999995


The Perceptron didn't fare very well mainly because the dataset is not linearly separated. On simpler datasets the algorithm performs much better, but unfortunately such datasets are rare in real life scenarios.

## AdaBoost

### Overview

**AdaBoost** is an algorithm which uses **ensemble learning**. In ensemble learning the hypotheses in the collection, or ensemble, vote for what the output should be and the output with the majority votes is selected as the final answer.

AdaBoost algorithm, as mentioned in the book, works with a **weighted training set** and **weak learners** (classifiers that have about 50%+epsilon accuracy i.e slightly better than random guessing). It manipulates the weights attached to the examples that are showed to it. Importance is given to the examples with higher weights.

<blockquote>
One way to think about this is that you have more to learn from your mistakes than
from your success.  If you predict X and are correct, you have nothing to learn.

<p>
If you predict X and are wrong, you made a mistake.  You need to update your model.  You have something to learn.
    
In the cognitive science world, this is known as <i>failure-driven learning</i>.
It is a powerful notion.

Think about it.  How do you know that you have something to learn?  You make a 
mistake.  You expected one outcome and something else happened.

Actually, you do not need to make a mistake.  Suppose you try something and expect
to fail.  If you actually succeed, you still have something to learn because 
you had an **expectation failure**.
    
</blockquote>

All the examples start with equal weights and a hypothesis is generated using these examples. Examples which are incorrectly classified, their weights are increased so that they can be classified correctly by the next hypothesis. The examples that are correctly classified, their weights are reduced. This process is repeated <i>K</i> times (here <i>K</i> is an input to the algorithm) and hence, <i>K</i> hypotheses are generated.

These <i>K</i> hypotheses are also assigned weights according to their performance on the weighted training set. The final ensemble hypothesis is the weighted-majority combination of these <i>K</i> hypotheses.

The speciality of AdaBoost is that by using weak learners and a sufficiently large *K*, a highly accurate classifier can be learned irrespective of the complexity of the function being learned or the dullness of the hypothesis space.

### Implementation

As seen in the previous section, the `PerceptronLearner` does not perform that well on the iris dataset. We'll use perceptron as the learner for the AdaBoost algorithm and try to increase the accuracy. 

Let's first see what AdaBoost is exactly:

In [230]:
psource(AdaBoost)

AdaBoost takes as inputs: <b>L</b> and <i>K</i> where <b>L</b> is the learner and <i>K</i> is the number of hypotheses to be generated. The learner <b>L</b> takes in as inputs: a dataset and the weights associated with the examples in the dataset. But the `PerceptronLearner` doesnot handle weights and only takes a dataset as its input.  
To remedy that we will give as input to the PerceptronLearner a modified dataset in which the examples will be repeated according to the weights associated to them. Intuitively, what this will do is force the learner to repeatedly learn the same example again and again until it can classify it correctly.   

To convert `PerceptronLearner` so that it can take weights as input too, we will have to pass it through the **`WeightedLearner`** function.

In [175]:
psource(WeightedLearner)

The `WeightedLearner` function will then call the `PerceptronLearner`, during each iteration, with the modified dataset which contains the examples according to the weights associated with them.

###  Example

We will pass the `PerceptronLearner` through `WeightedLearner` function. Then we will create an `AdaboostLearner` classifier with number of hypotheses or *K* equal to 5.

In [231]:
WeightedPerceptron = WeightedLearner(PerceptronLearner)
AdaboostLearner = AdaBoost(WeightedPerceptron, 5)

In [232]:
iris2 = DataSet(name="iris")
iris2.classes_to_numbers()

adaboost = AdaboostLearner(iris2)

adaboost([5, 3, 1, 0.1])

0

That is the correct answer. Let's check the error rate of adaboost with perceptron.

In [233]:
print("Error ratio for adaboost: ", err_ratio(adaboost, iris2))

Error ratio for adaboost:  0.033333333333333326


It reduced the error rate considerably. Unlike the `PerceptronLearner`, `AdaBoost` was able to learn the complexity in the iris dataset.

In [179]:
psource(err_ratio)